**Predicting Oscar-Nominated Screenplays with Sentence Embeddings**

Francis Gross   
Faculty of Informatics and Data Science  
University of Regensburg  
93053 Regensburg, Germany  
francis.gross@stud.uni-regensburg.de

In [78]:
# import:

import pandas as pd
import re, numpy as np
import unicodedata
import joblib
import torch

from pathlib import Path
from datasets import load_dataset
from sklearn.model_selection import train_test_split
from tqdm import tqdm
from sentence_transformers import SentenceTransformer
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import f1_score, accuracy_score, roc_auc_score, average_precision_score

In [79]:
# loading screeplay data from hugging-face: MovieSum

movie_sum_ds = load_dataset("rohitsaxena/MovieSum")

# to pandas
df_train = movie_sum_ds["train"].to_pandas()
df_val   = movie_sum_ds["validation"].to_pandas()
df_test  = movie_sum_ds["test"].to_pandas()

#display(df_train)
#display(df_val)
#display(df_test)

# concatinate all to one file for merging with nomination data
movie_sum_df = pd.concat([df_train, df_val, df_test], ignore_index=True)


# preparing and cleaning data for sentence embeddings

# extract title and year from movie_name
movie_sum_df[["title", "year"]] = movie_sum_df["movie_name"].str.extract(r"^(.*)_(\d{4})$")
movie_sum_df["year"] = movie_sum_df["year"].astype(float).astype("Int64")

#print(movie_sum_labeled.loc[0, 'script'])
# xml-tags in script, we need script_plain without tags
"""
<script>
<scene>
<stage_direction>..</stage_direction>
<scene_description>...</scene_description>
<character>..</character>
<dialogue>..</dialogue>
...
</scene>
<scene>
...
</scene>
<script>
"""
def strip_xml_tags(text):
    if text is None:
        return ""
    return re.sub(r"<[^>]+>", " ", str(text))

movie_sum_df["script_plain"] = movie_sum_df["script"].apply(strip_xml_tags)

# just to be safe, we clean script_plain by standards

# print(movie_sum_df.loc[0, 'script_plain'])

# regex

_REMOVE_LINE = re.compile(
    r"""
    ^\s*(                 # ganze Zeile prüfen
        page\s+\d+(\s+of\s+\d+)?     |  # "Page 12" / "Page 12 of 120"
        scanned\s+by.*                |  # Scans/Wasserzeichen
        downloaded\s+by.*            |
        transcribed\s+by.*           |
        copyright.*                  |
        all\s+rights\s+reserved.*    |
        [-=_]{3,}                       # Linien aus --- === ___
    )\s*$""",
    re.IGNORECASE | re.VERBOSE
)

_REMOVE_TRANSITION = re.compile(
    r"^\s*(CUT TO:|DISSOLVE TO:|SMASH CUT TO:|MATCH CUT TO:|FADE IN:|FADE OUT:)\s*$",
    re.IGNORECASE
)

_TIME_WORDS = r"(DAY|NIGHT|EVENING|MORNING|AFTERNOON|DAWN|DUSK|LATER|CONTINUOUS|SAME)"
_TIME_AT_END = re.compile(rf"\s*[-–—]{{1,2}}\s*{_TIME_WORDS}\s*$", re.IGNORECASE)
_TIME_ONLY   = re.compile(rf"^\s*[-–—]{{1,2}}\s*{_TIME_WORDS}\s*$", re.IGNORECASE)



def normalize_unicode(text):
    text = unicodedata.normalize("NFC", text)
    text = text.replace("\r\n", "\n").replace("\r", "\n").replace("\t", " ")
    text = (text
        .replace("\u00A0", " ")      
        .replace("\u2018", "'").replace("\u2019", "'")  # ‘ ’ -> '
        .replace("\u201C", '"').replace("\u201D", '"')  # “ ” -> "
        .replace("\u2013", "-").replace("\u2014", "-")  # – — -> -
    )
    return text


def clean_lines(text):
    out_lines = []
    for raw in text.split("\n"):
        line = raw.strip()
        if not line:
            out_lines.append("")  # keep structure
            continue
        if _REMOVE_LINE.match(line) or _REMOVE_TRANSITION.match(line):
            continue
        # reduce multiple spaces within the line
        line = re.sub(r"[ \u00A0]{2,}", " ", line)
        # normalize sluglines:
        #   "INT. OFFICE -- DAY"   -> "INT. OFFICE - DAY"
        #   "--NIGHT"              -> "NIGHT"
        #   "EXT. STREET – evening"-> "EXT. STREET - EVENING"
        line = _TIME_AT_END.sub(lambda m: f" - {m.group(1).upper()}", line)
        line = _TIME_ONLY.sub(lambda m: m.group(1).upper(), line)
        out_lines.append(line)
    # reduce multiple blank lines to max 1
    cleaned = "\n".join(out_lines)
    cleaned = re.sub(r"\n{3,}", "\n\n", cleaned).strip()
    return cleaned



def clean_script(text):
    text = normalize_unicode(text)
    text = clean_lines(text)
    return text

movie_sum_df["script_clean"] = movie_sum_df["script_plain"].apply(clean_script)


# just have a look at data
display(movie_sum_df)


Repo card metadata block was not found. Setting CardData to empty.


movie_name     imdb_id  \
0                          8MM_1999   tt0134273   
1                The Iron Lady_2011   tt1007029   
2                Adventureland_2009   tt1091722   
3                     Napoleon_2023  tt13287846   
4     Kubo and the Two Strings_2016   tt4302938   
...                             ...         ...   
2195      Terminator Salvation_2009   tt0438488   
2196         Collateral Damage_2002   tt0233469   
2197              Wonder Woman_2017   tt0451279   
2198                Flatliners_2017   tt2039338   
2199                   Vacancy_2007   tt0452702   

                                                 script  \
0     <script>\n  <scene>\n    <stage_direction>INT....   
1     <script>\n  <scene>\n    <stage_direction>INT....   
2     <script>\n  <scene>\n    <scene_description>Ad...   
3     <script>\n  <scene>\n    <character>NAPOLEON</...   
4     <script>\n  <scene>\n    <character>KUBO</char...   
...                                                 ...   
2195  <script>\n  <scene>\n    <stage_direction>INT....   
2196  <script>\n  <scene>\n    <stage_direction>INT....   
2197  <script>\n  <scene>\n    <scene_description>FA...   
2198  <script>\n  <scene>\n    <character>FLATLINERS...   
2199  <script>\n  <scene>\n    <character>VACANCY</c...   

                                                summary  \
0     Private investigator Tom Welles is contacted b...   
1     In flashbacks, the audience is shown a young M...   
2     In 1987, James Brennan plans to have a summer ...   
3     In 1793, amid the French Revolution, young arm...   
4     In feudal Japan, a 12-year-old boy with only o...   
...                                                 ...   
2195  In 2003, Dr. Serena Kogan of Cyberdyne Systems...   
2196  A bomb detonates in the plaza of the Colombian...   
2197  In present-day Paris, Diana Prince receives a ...   
2198  Courtney is a medical student who is obsessed ...   
2199  On their way home from a family party, David a...   

                         title  year  \
0                          8MM  1999   
1                The Iron Lady  2011   
2                Adventureland  2009   
3                     Napoleon  2023   
4     Kubo and the Two Strings  2016   
...                        ...   ...   
2195      Terminator Salvation  2009   
2196         Collateral Damage  2002   
2197              Wonder Woman  2017   
2198                Flatliners  2017   
2199                   Vacancy  2007   

                                           script_plain  \
0      \n   \n     INT.  MIAMI AIRPORT, TERMINAL -- ...   
1      \n   \n     INT. SHOP. NR CHESTER SQUARE. LON...   
2      \n   \n     AdVeNtUrElAnD by Greg Mottola rev...   
3      \n   \n     NAPOLEON \n     By \n     David S...   
4      \n   \n     KUBO \n     ... AND THE TWO STRIN...   
...                                                 ...   
2195   \n   \n     INT.   DEATH ROW/CELL - DAWN \n  ...   
2196   \n   \n     INT./EXT. NYFD FIREHOUSE - VARIOU...   
2197   \n   \n     FADE IN : \n     EXT. THE EARTH (...   
2198   \n   \n     FLATLINERS \n     By \n     Ben R...   
2199   \n   \n     VACANCY \n     by \n     Mark L S...   

                                           script_clean  
0     INT. MIAMI AIRPORT, TERMINAL - DAY\nAmongst th...  
1     INT. SHOP. NR CHESTER SQUARE. LONDON. PRESENT....  
2     AdVeNtUrElAnD by Greg Mottola revised August 5...  
3     NAPOLEON\nBy\nDavid Scarpa\n\nINT. TUILERIES -...  
4     KUBO\n... AND THE TWO STRINGS\nScreenplay by M...  
...                                                 ...  
2195  INT. DEATH ROW/CELL - DAWN\nLONGVIEW STATE COR...  
2196  INT./EXT. NYFD FIREHOUSE - VARIOUS SHOTS - NIG...  
2197  FADE IN :\nEXT. THE EARTH (FROM SPACE)\nThe EA...  
2198  FLATLINERS\nBy\nBen Ripley Based on a screenpl...  
2199  VACANCY\nby\nMark L Smith TheHalLieberman Comp...  

[2200 rows x 8 columns]

In [39]:
# read oscars.csv and extract nomination, win each FilmId to merge with MovieSum
# Oscar Class "Writing" and "Title" are used as screenplay data for the model

"""
use of oscars.csv under
BSD 2-Clause License

Copyright (c) 2022, David V. Lu!!
All rights reserved.

Redistribution and use in source and binary forms, with or without
modification, are permitted provided that the following conditions are met:

1. Redistributions of source code must retain the above copyright notice, this
   list of conditions and the following disclaimer.

2. Redistributions in binary form must reproduce the above copyright notice,
   this list of conditions and the following disclaimer in the documentation
   and/or other materials provided with the distribution.

THIS SOFTWARE IS PROVIDED BY THE COPYRIGHT HOLDERS AND CONTRIBUTORS "AS IS"
AND ANY EXPRESS OR IMPLIED WARRANTIES, INCLUDING, BUT NOT LIMITED TO, THE
IMPLIED WARRANTIES OF MERCHANTABILITY AND FITNESS FOR A PARTICULAR PURPOSE ARE
DISCLAIMED. IN NO EVENT SHALL THE COPYRIGHT HOLDER OR CONTRIBUTORS BE LIABLE
FOR ANY DIRECT, INDIRECT, INCIDENTAL, SPECIAL, EXEMPLARY, OR CONSEQUENTIAL
DAMAGES (INCLUDING, BUT NOT LIMITED TO, PROCUREMENT OF SUBSTITUTE GOODS OR
SERVICES; LOSS OF USE, DATA, OR PROFITS; OR BUSINESS INTERRUPTION) HOWEVER
CAUSED AND ON ANY THEORY OF LIABILITY, WHETHER IN CONTRACT, STRICT LIABILITY,
OR TORT (INCLUDING NEGLIGENCE OR OTHERWISE) ARISING IN ANY WAY OUT OF THE USE
OF THIS SOFTWARE, EVEN IF ADVISED OF THE POSSIBILITY OF SUCH DAMAGE.
"""

oscars_df = pd.read_csv("data/oscars.csv", sep="\t")
oscar_class = oscars_df.get("Class").astype(str).str.lower()

# we use "writing" and "title"
osc = oscars_df.loc[oscar_class.isin(["writing", "title"]), ["FilmId", "Winner"]].copy()

# we need the imdb_id to merge with MovieSum
osc["imdb_id"] = osc["FilmId"].astype(str).str.findall(r"tt\d+")
osc = osc.explode("imdb_id").dropna(subset=["imdb_id"])

# perhaps Oscar-Winner is needed later on, but for class writing and title no screenplay in MovieSum!
osc["winner"] = (osc["Winner"] == "True").astype(int)

#display(osc) #just have a look

# prepare and merge
labels_df = (
    osc.groupby("imdb_id", as_index=False)["winner"].max()
       .assign(nominated=1)[["imdb_id","nominated","winner"]])

movie_sum_labeled = movie_sum_df.merge(labels_df, on="imdb_id", how="left")
movie_sum_labeled["nominated"] = movie_sum_labeled["nominated"].fillna(0).astype(int)
movie_sum_labeled["winner"]    = movie_sum_labeled["winner"].fillna(0).astype(int)

# check data OK?
print(movie_sum_labeled[["imdb_id","movie_name","nominated","winner"]].head())
print("Sum:", len(movie_sum_labeled), "| nominated=1:", movie_sum_labeled["nominated"].sum(), "| winner=1:", movie_sum_labeled["winner"].sum())
print("\n\n")
display(movie_sum_labeled)

      imdb_id                     movie_name  nominated  winner
0   tt0134273                       8MM_1999          0       0
1   tt1007029             The Iron Lady_2011          0       0
2   tt1091722             Adventureland_2009          0       0
3  tt13287846                  Napoleon_2023          0       0
4   tt4302938  Kubo and the Two Strings_2016          1       0
Gesamt: 2200 | nominated=1: 417 | winner=1: 0





movie_name     imdb_id  \
0                          8MM_1999   tt0134273   
1                The Iron Lady_2011   tt1007029   
2                Adventureland_2009   tt1091722   
3                     Napoleon_2023  tt13287846   
4     Kubo and the Two Strings_2016   tt4302938   
...                             ...         ...   
2195      Terminator Salvation_2009   tt0438488   
2196         Collateral Damage_2002   tt0233469   
2197              Wonder Woman_2017   tt0451279   
2198                Flatliners_2017   tt2039338   
2199                   Vacancy_2007   tt0452702   

                                                 script  \
0     <script>\n  <scene>\n    <stage_direction>INT....   
1     <script>\n  <scene>\n    <stage_direction>INT....   
2     <script>\n  <scene>\n    <scene_description>Ad...   
3     <script>\n  <scene>\n    <character>NAPOLEON</...   
4     <script>\n  <scene>\n    <character>KUBO</char...   
...                                                 ...   
2195  <script>\n  <scene>\n    <stage_direction>INT....   
2196  <script>\n  <scene>\n    <stage_direction>INT....   
2197  <script>\n  <scene>\n    <scene_description>FA...   
2198  <script>\n  <scene>\n    <character>FLATLINERS...   
2199  <script>\n  <scene>\n    <character>VACANCY</c...   

                                                summary  \
0     Private investigator Tom Welles is contacted b...   
1     In flashbacks, the audience is shown a young M...   
2     In 1987, James Brennan plans to have a summer ...   
3     In 1793, amid the French Revolution, young arm...   
4     In feudal Japan, a 12-year-old boy with only o...   
...                                                 ...   
2195  In 2003, Dr. Serena Kogan of Cyberdyne Systems...   
2196  A bomb detonates in the plaza of the Colombian...   
2197  In present-day Paris, Diana Prince receives a ...   
2198  Courtney is a medical student who is obsessed ...   
2199  On their way home from a family party, David a...   

                         title  year  \
0                          8MM  1999   
1                The Iron Lady  2011   
2                Adventureland  2009   
3                     Napoleon  2023   
4     Kubo and the Two Strings  2016   
...                        ...   ...   
2195      Terminator Salvation  2009   
2196         Collateral Damage  2002   
2197              Wonder Woman  2017   
2198                Flatliners  2017   
2199                   Vacancy  2007   

                                           script_plain  \
0      \n   \n     INT.  MIAMI AIRPORT, TERMINAL -- ...   
1      \n   \n     INT. SHOP. NR CHESTER SQUARE. LON...   
2      \n   \n     AdVeNtUrElAnD by Greg Mottola rev...   
3      \n   \n     NAPOLEON \n     By \n     David S...   
4      \n   \n     KUBO \n     ... AND THE TWO STRIN...   
...                                                 ...   
2195   \n   \n     INT.   DEATH ROW/CELL - DAWN \n  ...   
2196   \n   \n     INT./EXT. NYFD FIREHOUSE - VARIOU...   
2197   \n   \n     FADE IN : \n     EXT. THE EARTH (...   
2198   \n   \n     FLATLINERS \n     By \n     Ben R...   
2199   \n   \n     VACANCY \n     by \n     Mark L S...   

                                           script_clean  nominated  winner  
0     INT. MIAMI AIRPORT, TERMINAL - DAY\nAmongst th...          0       0  
1     INT. SHOP. NR CHESTER SQUARE. LONDON. PRESENT....          0       0  
2     AdVeNtUrElAnD by Greg Mottola revised August 5...          0       0  
3     NAPOLEON\nBy\nDavid Scarpa\n\nINT. TUILERIES -...          0       0  
4     KUBO\n... AND THE TWO STRINGS\nScreenplay by M...          1       0  
...                                                 ...        ...     ...  
2195  INT. DEATH ROW/CELL - DAWN\nLONGVIEW STATE COR...          0       0  
2196  INT./EXT. NYFD FIREHOUSE - VARIOUS SHOTS - NIG...          0       0  
2197  FADE IN :\nEXT. THE EARTH (FROM SPACE)\nThe EA...          0       0  
2198  FLATLINERS\nBy\nBen Ripley B

In [ ]:
# path store dataframe local

outdir = Path("data/export_moviesum_oscar")
outdir.mkdir(parents=True, exist_ok=True)

parquet_path = outdir / "movie_sum_labeled.parquet"
movie_sum_labeled.to_parquet(parquet_path, index=False)

csv_path = outdir / "movie_sum_labeled.csv"
movie_sum_labeled.to_csv(csv_path, index=False)


In [ ]:
# upload to hugging face



In [41]:
# load data and split train val test

parquet_path = Path("data/export_moviesum_oscar/movie_sum_labeled.parquet")
df = pd.read_parquet(parquet_path)

y = df["nominated"].astype(int).to_numpy()
idx_all = np.arange(len(y))

# 60% train, 40% rest
idx_train, idx_rest, y_train, y_rest = train_test_split(idx_all, y , test_size=0.40, stratify=y, random_state=42)

# rest split to: 20% val, 20% test
idx_val, idx_test, y_val, y_test = train_test_split(idx_rest, y_rest, test_size=0.50, stratify=y_rest, random_state=42)

# check
print("Split sizes:",
      len(idx_train), "train ",
      len(idx_val), "val ",
      len(idx_test), "test")

print("Positive rate (nominated=1):")
print("  train:", y_train.mean())
print("  val:  ", y_val.mean())
print("  test: ", y_test.mean())

# store .npz - numpy zip format, easy to use
outdir = Path("data/splits")
outdir.mkdir(parents=True, exist_ok=True)

np.savez(outdir/"split_60_20_20.npz",
         idx_train=idx_train,
         idx_val=idx_val,
         idx_test=idx_test)


Split sizes: 1320 train | 440 val | 440 test
Positive rate (nominated=1):
  train: 0.1893939393939394
  val:   0.19090909090909092
  test:  0.18863636363636363
Splits saved to: data\splits\split_60_20_20.npz


In [81]:
# load splits
split_path = "data/splits/split_60_20_20.npz"
split = np.load(split_path)
idx_train, idx_val, idx_test = split["idx_train"], split["idx_val"], split["idx_test"]

print("Sizes    train:", len(idx_train), " val:", len(idx_val), " test:", len(idx_test))



Sizes    train: 1320  val: 440  test: 440


In [53]:
# chunking functions, prepare for embedder

def as_single_chunk(text):
    
    # return just one chunk (e.g. for titles)   
    return [text.strip()]

def chunk_text(text, max_words=400, overlap=80):
   
    # word-based chunking with overlap, max_words: number of words per chunk,  overlap to preserve context

    words = text.split()
    if not words:
        return [""]
        
    chunks = []
    i = 0
    step = max(1, max_words - overlap)
    
    while i < len(words):
        chunks.append(" ".join(words[i:i+max_words]))
        i += step
    return chunks

# chunking stats for report
def chunk_stats(list_of_chunks):
    n_chunks = np.array([len(x) for x in list_of_chunks], dtype=np.int32)
    return {
        "docs": len(n_chunks),
        "avg_chunks": float(n_chunks.mean()) if len(n_chunks) else 0.0,
        "max": int(n_chunks.max()) if len(n_chunks) else 0,
    }


In [76]:
# chunking title, summary, script_clean and storing in joblib

cache_dir = Path("chunks_cache")
cache_dir.mkdir(parents=True, exist_ok=True)

# title: just 1 chunk
title_chunks_path = cache_dir / "title_chunks.joblib"
if title_chunks_path.exists():
    title_chunks = joblib.load(title_chunks_path)
else:
    title_chunks = [as_single_chunk(t) for t in tqdm(df["title"].fillna("").astype(str).tolist(), desc="chunking title")]
    joblib.dump(title_chunks, title_chunks_path)

# summary: word-based chunking
summary_chunks_path = cache_dir / "summary_chunks.joblib"
if summary_chunks_path.exists():
    summary_chunks = joblib.load(summary_chunks_path)
else:
    summary_chunks = [chunk_text(s, max_words=400, overlap=80) for s in tqdm(df["summary"].fillna("").astype(str).tolist(), desc="chunking summary")]
    joblib.dump(summary_chunks, summary_chunks_path)

# script_clean: word-based chunking
script_chunks_path = cache_dir / "script_clean_chunk.joblib"
if script_chunks_path.exists():
    script_chunks = joblib.load(script_chunks_path)
else:
    script_chunks = [chunk_text(s, max_words=400, overlap=80) for s in tqdm(df["script_clean"].fillna("").astype(str).tolist(), desc="chunking script_clean")]
    joblib.dump(script_chunks, script_chunks_path)

# print stats for report
print("\nchunking stats:")
print("title  :", chunk_stats(title_chunks))
print("summary:", chunk_stats(summary_chunks))
print("script :", chunk_stats(script_chunks))


Chunking script_clean: 100%|██████████████████████████████████████████████████████| 2200/2200 [00:17<00:00, 127.06it/s]



chunking stats:
title  : {'docs': 2200, 'avg_chunks': 1.0, 'max': 1}
summary: {'docs': 2200, 'avg_chunks': 2.505909090909091, 'max': 6}
script : {'docs': 2200, 'avg_chunks': 77.03818181818181, 'max': 186}


In [75]:
# check chunks e.g. movie 8MM
i = 0  

print("Movie:", df.iloc[i]["movie_name"])
print("\nTitle chunks:", title_chunks[i])

print("\nSummary - number of chunks:", len(summary_chunks[i]))
print("Summary - first chunk:")
print(summary_chunks[i][0][:200], "...")

print("\nScript - number of chunks:", len(script_chunks[i]))
print("Script - first chunk:")
print(script_chunks[i][0][:200], "...")


Movie: 8MM_1999

Title chunks: ['8MM']

Summary - number of chunks: 3
Summary - first chunk:
Private investigator Tom Welles is contacted by Daniel Longdale, attorney for wealthy widow Mrs. Christian, whose husband has recently died. While clearing out her late husband's safe, she and Longdal ...

Script - number of chunks: 115
Script - first chunk:
INT. MIAMI AIRPORT, TERMINAL - DAY Amongst the weary tourist families and solitary businessmen sits TOM WELLES , middle - aged , hair neat , suit crisp and gray . He 's eating crackers from a cellopha ...


In [58]:
# load model intfloat/e5-base-v2, GPU/FP16 if CUDA available (nvidia geforce RTX 3060, 12 GB VRAM)

device = "cuda" if torch.cuda.is_available() else "cpu"
embedder = SentenceTransformer("intfloat/e5-base-v2", device=device)

if device == "cuda":
    embedder = embedder.to(torch.float16)  # FP16 float16 for faster run and less VRAM  (instead of FP32)

# encoding function for sentence embeddings
def encode_chunks(chunks, batch_size=96):
    
    texts = [f"query: {c}" for c in chunks]    # präfix: "query:" for classification as learned from https://huggingface.co/intfloat/e5-base-v2
    embs = embedder.encode(
        texts,
        batch_size=batch_size,                # batch_size = 96 should work
        normalize_embeddings=True,
        show_progress_bar=False
    )
    return np.asarray(embs, dtype=np.float32)  # float32 is standard, probably even 64bit internal is slower

# mean max pooling function and normalize L2
def pool_mean_max(embs: np.ndarray):
    
    mu = embs.mean(axis=0)
    mx = embs.max(axis=0)
    vec = np.concatenate([mu, mx], axis=0)
    n = np.linalg.norm(vec) + 1e-12
    return (vec / n).astype(np.float32)
    
    

In [82]:

emb_dir = Path("emb_cache")
emb_dir.mkdir(parents=True, exist_ok=True)

def compute_script_embeddings(chunks_per_doc, cache_file, batch_size=96, desc=""):
   
    cache_path = emb_dir / cache_file   # make path of emb_dir and "cache_file"
    if cache_path.exists():
        X = joblib.load(cache_path)
        print(f"Loaded from cache: {cache_path}   Shape: {X.shape}")
        return X

    vecs = []
    for chs in tqdm(chunks_per_doc, desc=desc):
        embs = encode_chunks(chs, batch_size=batch_size)   # E5, FP16 encoding
        vec  = pool_mean_max(embs)                         # mean, max, L2-normalize
        vecs.append(vec)
    X = np.vstack(vecs).astype(np.float32)
    joblib.dump(X, cache_path)                             # store embeddings in joblib
    print(f"Stored: {cache_path}   Shape: {X.shape}")
    return X
    

# titel embeddings
X_title = compute_script_embeddings(
    title_chunks,                              # from joblib
    cache_file="emb_title.joblib",
    batch_size=256,                            # 256 batch size is possible
    desc="encode title"
)

# summary embeddings
X_summary = compute_script_embeddings(
    summary_chunks,                           # from joblib
    cache_file="emb_summary.joblib",
    batch_size=96,                            # default batch size
    desc="encode summary"
)

# script_clean embeddings
X_script = compute_script_embeddings(
    script_chunks,                            # from joblib
    cache_file="emb_script.joblib",
    batch_size=96,                            # default batch size
    desc="encode script"
)

# check embeddings 
print("\nEmbeddings done:")
print("  X_title  :", X_title.shape,  X_title.dtype)
print("  X_summary:", X_summary.shape, X_summary.dtype)
print("  X_script :", X_script.shape,  X_script.dtype)


Loaded from cache: emb_cache\emb_title.joblib   Shape: (2200, 1536)
Loaded from cache: emb_cache\emb_summary.joblib   Shape: (2200, 1536)
Loaded from cache: emb_cache\emb_script.joblib   Shape: (2200, 1536)

Embeddings done:
  X_title  : (2200, 1536) float32
  X_summary: (2200, 1536) float32
  X_script : (2200, 1536) float32


In [60]:
# load embeddings and splits

emb_dir = Path("emb_cache")

X_title   = joblib.load(emb_dir / "emb_title.joblib")        # all titel!!! -> train, val, test indexed!!!
X_summary = joblib.load(emb_dir / "emb_summary.joblib")      # all summaries!!! -> train, val, test indexed!!!
X_script  = joblib.load(emb_dir / "emb_script.joblib")       # all scripts!!! -> train, val, test indexed!!!

print("Shapes:")
print("  title  :", X_title.shape)
print("  summary:", X_summary.shape)
print("  script :", X_script.shape)


y_all = df["nominated"].astype(int).to_numpy()                # all scripts nominated: 0 or 1 -> indexed!!!

split = np.load("data/splits/split_60_20_20.npz")
idx_train, idx_val, idx_test = split["idx_train"], split["idx_val"], split["idx_test"]

# check splits 60/20/20
print("Split sizes:", len(idx_train), len(idx_val), len(idx_test))

Shapes:
  title  : (2200, 1536)
  summary: (2200, 1536)
  script : (2200, 1536)
Split sizes: 1320 440 440


In [83]:
# train, val, test logistic regression function on variants: single features or combined features


def train_eval_variant(X, y_all, idx_train, idx_val, idx_test, name="VARIANT"):
    # use index for splits
    X_train, X_val, X_test = X[idx_train], X[idx_val], X[idx_test]
    y_train, y_val, y_test = y_all[idx_train], y_all[idx_val], y_all[idx_test]

    # logistic regression
    clf = LogisticRegression(
        max_iter=5000,                # hyperparameter described in report paper
        class_weight="balanced",
        C=1.0,
        n_jobs=4                      # use 4 cpu kernel if possible
    )

    # training
    clf.fit(X_train, y_train)

    # threshold tuning
    val_probs = clf.predict_proba(X_val)[:, 1]
    ths = np.linspace(0.05, 0.95, 181)            # step size 0,005!
    f1s = [f1_score(y_val, (val_probs >= t).astype(int)) for t in ths]
    best_t = ths[int(np.argmax(f1s))]

    # predicting
    test_probs = clf.predict_proba(X_test)[:, 1]
    test_pred  = (test_probs >= best_t).astype(int)

    acc  = accuracy_score(y_test, test_pred)
    roc  = roc_auc_score(y_test, test_probs)
    pr   = average_precision_score(y_test, test_probs)  # PR-AUC
    f1_p = f1_score(y_test, test_pred, pos_label=1)
    f1_n = f1_score(y_test, test_pred, pos_label=0)
    f1_m = 0.5 * (f1_p + f1_n)


    # data for reports table
    print(f"\n=== {name} ===")
    print(f"Best val threshold: {best_t:.2f}")
    print("Accuracy :", acc)
    print("ROC-AUC  :", roc)
    print("PR-AUC   :", pr)
    print("F1_pos   :", f1_p)
    print("F1_neg   :", f1_n)
    print("Macro-F1 :", f1_m)

    # return results for further use
    return {
        "variant": name,
        "best_t_val": float(best_t),
        "ACC_test": float(acc),
        "ROC_AUC_test": float(roc),
        "PR_AUC_test": float(pr),
        "F1_pos_test": float(f1_p),
        "F1_neg_test": float(f1_n),
        "Macro_F1_test": float(f1_m),
        "model": clf,
    }



In [86]:
# result computing for feature variants

res_title = train_eval_variant(X_title, y_all, idx_train, idx_val, idx_test, name="TITLE")

res_script = train_eval_variant(X_script, y_all, idx_train, idx_val, idx_test, name="SCRIPT")

res_summary = train_eval_variant(X_summary, y_all, idx_train, idx_val, idx_test, name="SUMMARY")

res_script_summary = train_eval_variant(np.hstack([X_script, X_summary]), y_all, idx_train, idx_val, idx_test, name="SCRIPT+SUMMARY") # horizontal numpy stack for combination

res_script_summary_title = train_eval_variant(np.hstack([X_script, X_summary, X_title]), y_all, idx_train, idx_val, idx_test, name="SCRIPT+SUMMARY+TITLE") # horizontal numpy stack for combination



=== TITLE ===
Best val threshold: 0.49
Accuracy : 0.6704545454545454
ROC-AUC  : 0.6919104991394148
PR-AUC   : 0.34683336198805464
F1_pos   : 0.3881856540084388
F1_neg   : 0.7744945567651633
Macro-F1 : 0.581340105386801

=== SCRIPT ===
Best val threshold: 0.52
Accuracy : 0.7318181818181818
ROC-AUC  : 0.7419256859370255
PR-AUC   : 0.4154771297314072
F1_pos   : 0.42718446601941745
F1_neg   : 0.8249258160237388
Macro-F1 : 0.6260551410215781

=== SUMMARY ===
Best val threshold: 0.50
Accuracy : 0.6931818181818182
ROC-AUC  : 0.7537038911950322
PR-AUC   : 0.4243557395687297
F1_pos   : 0.4444444444444444
F1_neg   : 0.7880690737833596
Macro-F1 : 0.616256759113902

=== SCRIPT+SUMMARY ===
Best val threshold: 0.51
Accuracy : 0.7340909090909091
ROC-AUC  : 0.7675744996793898
PR-AUC   : 0.450240232910733
F1_pos   : 0.4845814977973568
F1_neg   : 0.8208269525267994
Macro-F1 : 0.652704225162078

=== SCRIPT+SUMMARY+TITLE ===
Best val threshold: 0.52
Accuracy : 0.759090909090909
ROC-AUC  : 0.7900172117039

In [87]:


results_df = pd.DataFrame([
    res_title, res_script, res_summary,
    res_script_summary, res_script_summary_title
])

# overview
print(results_df.drop(columns=["model"]).sort_values("PR_AUC_test", ascending=False))


                variant  best_t_val  ACC_test  ROC_AUC_test  PR_AUC_test  \
4  SCRIPT+SUMMARY+TITLE       0.520  0.759091      0.790017     0.455348   
3        SCRIPT+SUMMARY       0.510  0.734091      0.767574     0.450240   
2               SUMMARY       0.500  0.693182      0.753704     0.424356   
1                SCRIPT       0.520  0.731818      0.741926     0.415477   
0                 TITLE       0.495  0.670455      0.691910     0.346833   

   F1_pos_test  F1_neg_test  Macro_F1_test  
4     0.485437     0.842730       0.664083  
3     0.484581     0.820827       0.652704  
2     0.444444     0.788069       0.616257  
1     0.427184     0.824926       0.626055  
0     0.388186     0.774495       0.581340  
